In [1]:
using Random
Random.seed!(13)

using CSV
using Plots
using DataFrames
using Statistics
using Missings
using Distributions
using StatsPlots
using LowRankModels, LinearAlgebra

In [2]:
include("proxgrad.jl")
df = CSV.read("airline.csv")

41396×20 DataFrame. Omitted printing of 18 columns
│ Row   │ airline_name  │ link                           │
│       │ String        │ String                         │
├───────┼───────────────┼────────────────────────────────┤
│ 1     │ adria-airways │ /airline-reviews/adria-airways │
│ 2     │ adria-airways │ /airline-reviews/adria-airways │
│ 3     │ adria-airways │ /airline-reviews/adria-airways │
│ 4     │ adria-airways │ /airline-reviews/adria-airways │
│ 5     │ adria-airways │ /airline-reviews/adria-airways │
│ 6     │ adria-airways │ /airline-reviews/adria-airways │
│ 7     │ adria-airways │ /airline-reviews/adria-airways │
│ 8     │ adria-airways │ /airline-reviews/adria-airways │
│ 9     │ adria-airways │ /airline-reviews/adria-airways │
│ 10    │ adria-airways │ /airline-reviews/adria-airways │
⋮
│ 41386 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41387 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41388 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41389 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41390 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41391 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41392 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41393 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41394 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41395 │ wizz-air      │ /airline-reviews/wizz-air      │
│ 41396 │ wizz-air      │ /airline-reviews/wizz-air      │

In [3]:
# Organize and display features along with variable type
feature_names = names(df)
for i in 1:20
    println(string(i), "\t", string(feature_names[i]), "\t\t\t", string(eltype(df[!, i])))
end

1	airline_name			String
2	link			String
3	title			String
4	author			String
5	author_country			Union{Missing, String}
6	date			Dates.Date
7	content			String
8	aircraft			Union{Missing, String}
9	type_traveller			Union{Missing, String}
10	cabin_flown			Union{Missing, String}
11	route			Union{Missing, String}
12	overall_rating			Union{Missing, Float64}
13	seat_comfort_rating			Union{Missing, Float64}
14	cabin_staff_rating			Union{Missing, Float64}
15	food_beverages_rating			Union{Missing, Float64}
16	inflight_entertainment_rating			Union{Missing, Float64}
17	ground_service_rating			Union{Missing, Float64}
18	wifi_connectivity_rating			Union{Missing, Float64}
19	value_money_rating			Union{Missing, Float64}
20	recommended			Int64


In [4]:
# df = df[1:10000,:]

In [5]:
# Reduce number of datapoints for computation time

# Filter data to only consider entries with overall rating
df_OR = df[.!(ismissing.(df[!, :overall_rating])), :];

df_OR_filtered = df_OR[.!(ismissing.(df_OR[!, :seat_comfort_rating])), :]; 
data_OR_filtered = df_OR_filtered[.!(ismissing.(df_OR_filtered[!, :cabin_staff_rating])), :];

# Now adding food_beverages_rating, inflight_entertainment_rating, and value money rating
data_OR_filtered = data_OR_filtered[.!(ismissing.(data_OR_filtered[!, :food_beverages_rating])), :];
data_OR_filtered = data_OR_filtered[.!(ismissing.(data_OR_filtered[!, :inflight_entertainment_rating])), :];
data_OR_filtered = data_OR_filtered[.!(ismissing.(data_OR_filtered[!, :value_money_rating])), :];

train_proportion = 0.8
n = size(data_OR_filtered, 1)
println("Size of dataset: ", string(n))

# Put the first ntrain observations in the DataFrame df into the training set, and the rest into the test set
ntrain = convert(Int, round(train_proportion*n))
println("Size of train: ", string(round(train_proportion*n)))
println("Size of test: ", string(round(n-train_proportion*n)))

target = data_OR_filtered[:, :recommended]

# Filter data for entries with only seat_comfort, cabin_staff
# df_OR_filtered = df_OR[.!(ismissing.(df[!, :seat_comfort_rating])), :]; 
# df_OR_filtered = df_OR[.!(ismissing.(df[!, :cabin_staff_rating])), :]; 
# data_OR_filtered = df_OR_filtered[:, filter(col -> (col != :overall_rating), feature_names)]

# the following variable records the features of examples in the training set
train_x = data_OR_filtered[1:ntrain,:]

# the following variable records the features of examples in the test set
test_x = data_OR_filtered[ntrain+1:end,:]

# the following variable records the labels of examples in the training set
train_y = target[1:ntrain]
train_y = collect(skipmissing(train_y))
# the following variable records the labels of examples in the test set
test_y = target[ntrain+1:end]
test_y = collect(skipmissing(test_y));

Size of dataset: 28341
Size of train: 22673.0
Size of test: 5668.0


In [6]:
"""This function just computes the mean squared error."""
function MSE(y, pred)
    "Fill this in."
    num = size(y,1)
    error = sum(abs.((y.-pred).^2))/num
    return error
end

"""This function plots the main diagonal; 
for a "predicted vs true" plot with perfect predictions,
all data lies on this line"""
function plotDiagonal(xmin, xmax)
    xsamples = [xmin, xmax]
    plot!(xsamples, xsamples, color=:black)
end

"""This helper funciton plots x vs, y and labels the axes."""
function plotdata(x,y,xname, yname; margin=.05, plotDiag=true, zeromin=false)
    scatter(x,y, label="data")
    xlabel!(xname)
    ylabel!(yname)
    range_y = maximum(y) - minimum(y)
    range_x = maximum(x) - minimum(x)
    if plotDiag
        plotDiagonal(minimum(x)-margin*range_x, maximum(x)+margin*range_x)
    end
    if zeromin
        ylims!((0.0,maximum(y)+margin*range_y))
        xlims!((0.0,maximum(x)+margin*range_x))
    else
        ylims!((minimum(y)-margin*range_y,maximum(y)+margin*range_y))
        xlims!((minimum(x)-margin*range_x,maximum(x)+margin*range_x))
    end
end

"""This function plots the predicted labels vs the actual labels
(We only plots the first 1000 points to avoid slow plots.)"""
function plot_pred_true(test_pred, test_y, max_points = 1000)
    plotdata(test_pred[1:max_points], test_y[1:max_points], "Predicted Rating", "True Rating", zeromin=true)
end

plot_pred_true

In [7]:
"This function converts strings to floating point values.
Strings that cannot be represented as a number (like NA) are converted to zeros"
function string_to_float(str)
    try
        parse(Float64, str)
    catch
       0.0
    end
end

labels_real = [
  :overall_rating,
  :seat_comfort_rating,
  :cabin_staff_rating,
  :food_beverages_rating,
  :inflight_entertainment_rating,
  :ground_service_rating,
  :wifi_connectivity_rating,
  :value_money_rating,
  :recommended
]

labels_string = [
    :beds,
    :security_deposit,
    :cleaning_fee
]

3-element Array{Symbol,1}:
 :beds            
 :security_deposit
 :cleaning_fee    

In [8]:
# # Only converting for seat comfort and cabin staff
# train_vals_real = convert(Matrix,train_x[:,filter(col -> (col in labels_real), [:seat_comfort_rating,:cabin_staff_rating])]);
# test_vals_real = convert(Matrix,test_x[:,filter(col -> (col in labels_real), [:seat_comfort_rating,:cabin_staff_rating])]);
# size(train_vals_real,1)
# any(ismissing,train_vals_real)

# Only converting for seat comfort, cabin staff, food/beverage, and inflight entertainment
train_vals_real = convert(Matrix,train_x[:,filter(col -> (col in labels_real), [:seat_comfort_rating,:cabin_staff_rating,:food_beverages_rating,:inflight_entertainment_rating,:value_money_rating])]);
test_vals_real = convert(Matrix,test_x[:,filter(col -> (col in labels_real), [:seat_comfort_rating,:cabin_staff_rating,:food_beverages_rating,:inflight_entertainment_rating,:value_money_rating])]);
size(train_vals_real,1)
any(ismissing,train_vals_real)
train_vals_real = convert(Array{Float64,2},train_vals_real)

# Add offset
train_vals_real = [train_vals_real ones(size(train_vals_real,1))];
test_vals_real = [test_vals_real ones(size(test_vals_real,1))];

[train_vals_real train_y]

22673×7 Array{Float64,2}:
 4.0  4.0  4.0  0.0  4.0  1.0  1.0
 4.0  5.0  4.0  1.0  5.0  1.0  1.0
 5.0  5.0  4.0  0.0  5.0  1.0  1.0
 4.0  4.0  3.0  1.0  4.0  1.0  1.0
 4.0  2.0  1.0  2.0  2.0  1.0  0.0
 4.0  4.0  3.0  3.0  4.0  1.0  1.0
 4.0  4.0  1.0  0.0  3.0  1.0  1.0
 5.0  5.0  4.0  3.0  4.0  1.0  1.0
 4.0  3.0  4.0  1.0  4.0  1.0  1.0
 5.0  5.0  4.0  4.0  4.0  1.0  1.0
 4.0  4.0  4.0  4.0  4.0  1.0  1.0
 4.0  5.0  3.0  3.0  5.0  1.0  1.0
 4.0  4.0  4.0  0.0  4.0  1.0  1.0
 ⋮                        ⋮       
 1.0  1.0  1.0  1.0  1.0  1.0  0.0
 2.0  1.0  1.0  1.0  1.0  1.0  0.0
 1.0  2.0  1.0  1.0  1.0  1.0  0.0
 1.0  2.0  2.0  1.0  1.0  1.0  0.0
 2.0  4.0  3.0  1.0  2.0  1.0  0.0
 1.0  2.0  1.0  1.0  1.0  1.0  0.0
 1.0  1.0  1.0  1.0  1.0  1.0  0.0
 1.0  1.0  1.0  1.0  1.0  1.0  0.0
 1.0  1.0  1.0  1.0  1.0  1.0  0.0
 5.0  5.0  2.0  3.0  5.0  1.0  1.0
 2.0  4.0  2.0  1.0  3.0  1.0  1.0
 1.0  1.0  1.0  1.0  1.0  1.0  0.0

# Logistic Loss 

In [9]:
test_ybool = Int.(sign.(test_y))
train_ybool = Int.(sign.(train_y))

test_ybool[test_ybool.==0] .= -1
train_ybool[train_ybool.==0] .= -1

# Logistical Loss
loss_log = 1/n*LogisticLoss()

reg = ZeroReg()
w_log = proxgrad(loss_log, reg, train_vals_real, train_ybool, maxiters=10000) 

6-element Array{Float64,1}:
  0.5131805981313962  
  0.7835474384376433  
  0.2006748083051536  
  0.046745004680577004
  1.2171126853379022  
 -8.53278400169754    

In [10]:
# Log loss misclassification on training set
n2 = length(train_ybool)
misclass_train = (n2 - sum(sign.(train_vals_real*w_log) .== train_ybool)) / n2

# Log loss misclassification on testing set
n = length(test_ybool)
misclass_test = (n - sum(sign.(test_vals_real*w_log) .== test_ybool)) / n

println("Training Misclassification Rate:\t", misclass_train)
println("Testing Misclassification Rate:\t", misclass_test)

Training Misclassification Rate:	0.08177126979226393
Testing Misclassification Rate:	0.07868736767819337


In [11]:
z = train_vals_real*w_log
scatter(z, train_y, label = "data y")
plot!(sort(z), sort(1 ./(1 .+exp.(-z))), label = "prediction")
# ylim(-.1, 1.1)
# legend(loc=2)
# xlabel("w^Tx")
# ylabel("y")
xlabel!("w^Tx")
ylabel!("y")

# Hinge Loss

In [12]:
loss_hinge = 1/n*HingeLoss()
reg = ZeroReg()
w_hinge = proxgrad(loss_hinge, reg, train_vals_real, train_ybool, maxiters=5000) 

6-element Array{Float64,1}:
  0.16148162446784697   
  0.32455897246337845   
  0.06946939818285741   
 -1.5954750200836848e-10
  0.5270467535521118    
 -3.2607575965015645    

In [13]:
# Log loss misclassification on training set
n2 = length(train_ybool)
misclass_train = (n2 - sum(sign.(train_vals_real*w_hinge) .== train_ybool)) / n2

# Log loss misclassification on testing set
n = length(test_ybool)
misclass_test = (n - sum(sign.(test_vals_real*w_hinge) .== test_ybool)) / n

println("Training Misclassification Rate:\t", misclass_train)
println("Testing Misclassification Rate:\t", misclass_test)

Training Misclassification Rate:	0.08666696070215675
Testing Misclassification Rate:	0.08151023288637968
